In [1]:
from bs4 import BeautifulSoup as bs
import itertools
from itertools import combinations
import re
import pandas as pd
import numpy as np

### Открываем размеченный дневник формата xml

In [2]:
f = open('Marked_text.xml')
diary = f.read()
f.close()
soup = bs(diary, 'xml')

###  Открываем список английских аналогов русских фамилий и прозвищ

In [27]:
with open('List_of_refs_clear.txt', 'r') as f:
    lines = f.readlines()
    all_surnames = ['#'+line for line in lines]
    all_surnames = [line[:-1] for line in all_surnames]
    all_surnames = sorted(all_surnames)

### Создаем all_mentions = список списков, внутри которых лежат упоминания людей в одном параграфе дневника

In [29]:
all_mentions = []
for par in soup.find_all('p'):
    mentioned_ref = list(set([persName.get('ref') for persName in par.find_all('persName')]))
    if len(mentioned_ref) != 0:
        all_mentions.append(mentioned_ref)

### Создаем mentions_table - таблицу-матрицу, в которой будут обозначены встречи/пересечения/упоминания людей в одном параграфе

In [30]:
mentions_table = pd.DataFrame(np.zeros(shape=(len(all_surnames), len(all_surnames))), 
                             columns=sorted(all_surnames), index=sorted(all_surnames))
# pd.set_option('display.max_rows', 308)
# pd.set_option('display.max_columns', 308)

#abramovich  #adamovich  #afonskij  #aga  #ajhenval'd  \
#abramovich                     0.0         0.0        0.0   0.0          0.0   
#adamovich                      0.0         0.0        0.0   0.0          0.0   
#afonskij                       0.0         0.0        0.0   0.0          0.0   
#aga                            0.0         0.0        0.0   0.0          0.0   
#ajhenval'd                     0.0         0.0        0.0   0.0          0.0   
#al'tshulera                    0.0         0.0        0.0   0.0          0.0   
#aldanov                        0.0         0.0        0.0   0.0          0.0   
#aldanovy                       0.0         0.0        0.0   0.0          0.0   
#aleksinskaja                   0.0         0.0        0.0   0.0          0.0   
#amfiteatrov                    0.0         0.0        0.0   0.0          0.0   
#aminad                         0.0         0.0        0.0   0.0          0.0   
#bal'mont                       0.0         0.0        0.0   0.0          0.0   
#baratov                        0.0         0.0        0.0   0.0          0.0   
#beek                           0.0         0.0        0.0   0.0          0.0   
#belich                         0.0         0.0        0.0   0.0          0.0   
#beljaev                        0.0         0.0        0.0   0.0          0.0   
#berberova                      0.0         0.0        0.0   0.0          0.0   
#brezhnev                       0.0         0.0        0.0   0.0          0.0   
#brezhnevy                      0.0         0.0        0.0   0.0          0.0   
#bunakov-fondaminskij           0.0         0.0        0.0   0.0          0.0   
#bunin                          0.0         0.0        0.0   0.0          0.0   
#bunina                         0.0         0.0        0.0   0.0          0.0   
#buniny                         0.0         0.0        0.0   0.0          0.0   
#burd                           0.0         0.0        0.0   0.0          0.0   
#chasing                        0.0         0.0        0.0   0.0          0.0   
#chirikov                       0.0         0.0        0.0   0.0          0.0   
#dali                           0.0         0.0        0.0   0.0          0.0   
#demidov                        0.0         0.0        0.0   0.0          0.0   
#demidova                       0.0         0.0        0.0   0.0          0.0   
#denikin                        0.0         0.0        0.0   0.0          0.0   
#dioneo                         0.0         0.0        0.0   0.0          0.0   
#don-aminado                    0.0         0.0        0.0   0.0          0.0   
#el'jashevich                   0.0         0.0        0.0   0.0          0.0   
#elpat'evskij                   0.0         0.0        0.0   0.0          0.0   
#eremeeva                       0.0         0.0        0.0   0.0          0.0   
#evlogij                        0.0         0.0        0.0   0.0          0.0   
#fedotov                        0.0         0.0        0.0   0.0          0.0   
#filosofov                      0.0         0.0        0.0   0.0          0.0   
#fondaminskaja                  0.0         0.0        0.0   0.0          0.0   
#fondaminskie                   0.0         0.0        0.0   0.0          0.0   
#fondaminskij                   0.0         0.0        0.0   0.0          0.0   
#gerber                         0.0         0.0        0.0   0.0          0.0   
#gessen                         0.0         0.0        0.0   0.0          0.0   
#gippius                        0.0         0.0        0.0   0.0          0.0   
#glazunov                       0.0         0.0        0.0   0.0          0.0   
#goncharova                     0.0         0.0        0.0   0.0          0.0   
#gor'kie                        0.0         0.0        0.0   0.0          0.0   
#gor'kij                        0.0         0.0        0.0   0.0          0.0   
#guchkov                        0.0         0.0        

### Создаем функцию, которая считает пары людей

In [31]:
def add_person_2_table(mentions_table, surname_list):
    if len(surname_list)>1:
        for surname_1 in surname_list:
            for surname_2 in surname_list:
                mentions_table.at[surname_1, surname_2] += 1 #dataframe.at - фишка pandas, благодаря чему на пересечении двух фамилий прибавляется единица
    else: #Вот тут проблема - что делать с людьми, которые упоминаются отдельно от кого-либо и которых не с кем считать
        for surname in surname_list:
            mentions_table.at[surname, surname] += 1
    return mentions_table

### Для каждого списка в списке all_mentions применяем нашу функцию

In [32]:
for surname_list in all_mentions:
    add_person_2_table(mentions_table, surname_list)

In [33]:
mentions_table

#abramovich  #adamovich  #afonskij  #aga  #ajhenval'd  \
#abramovich                     1.0         0.0        0.0   0.0          0.0   
#adamovich                      0.0         4.0        0.0   0.0          0.0   
#afonskij                       0.0         0.0        1.0   0.0          0.0   
#aga                            0.0         0.0        0.0   3.0          0.0   
#ajhenval'd                     0.0         0.0        0.0   0.0          1.0   
#al'tshulera                    0.0         0.0        0.0   0.0          0.0   
#aldanov                        0.0         0.0        0.0   0.0          0.0   
#aldanovy                       0.0         0.0        0.0   0.0          0.0   
#aleksinskaja                   0.0         0.0        0.0   0.0          0.0   
#amfiteatrov                    0.0         0.0        0.0   0.0          0.0   
#aminad                         0.0         0.0        0.0   0.0          0.0   
#bal'mont                       0.0         0.0        0.0   0.0          0.0   
#baratov                        0.0         0.0        0.0   0.0          0.0   
#beek                           0.0         0.0        0.0   0.0          0.0   
#belich                         0.0         0.0        0.0   0.0          0.0   
#beljaev                        0.0         0.0        0.0   0.0          0.0   
#berberova                      0.0         0.0        0.0   0.0          0.0   
#brezhnev                       0.0         0.0        0.0   0.0          0.0   
#brezhnevy                      0.0         0.0        0.0   0.0          0.0   
#bunakov-fondaminskij           0.0         0.0        0.0   0.0          0.0   
#bunin                          0.0         0.0        0.0   0.0          0.0   
#bunina                         0.0         0.0        0.0   0.0          0.0   
#buniny                         0.0         0.0        0.0   0.0          0.0   
#burd                           0.0         0.0        0.0   0.0          0.0   
#chasing                        0.0         0.0        0.0   0.0          0.0   
#chirikov                       0.0         0.0        0.0   0.0          0.0   
#dali                           0.0         0.0        0.0   0.0          0.0   
#demidov                        0.0         0.0        0.0   0.0          0.0   
#demidova                       0.0         0.0        1.0   0.0          0.0   
#denikin                        0.0         0.0        0.0   0.0          0.0   
#dioneo                         0.0         0.0        0.0   0.0          0.0   
#don-aminado                    0.0         0.0        0.0   0.0          0.0   
#el'jashevich                   0.0         0.0        0.0   0.0          0.0   
#elpat'evskij                   0.0         0.0        0.0   0.0          0.0   
#eremeeva                       0.0         0.0        0.0   0.0          0.0   
#evlogij                        0.0         0.0        1.0   0.0          0.0   
#fedotov                        0.0         0.0        0.0   0.0          0.0   
#filosofov                      0.0         0.0        0.0   0.0          0.0   
#fondaminskaja                  0.0         0.0        0.0   0.0          0.0   
#fondaminskie                   0.0         0.0        0.0   0.0          0.0   
#fondaminskij                   1.0         1.0        0.0   0.0          0.0   
#gerber                         0.0         0.0        0.0   0.0          0.0   
#gessen                         0.0         0.0        0.0   0.0          0.0   
#gippius                        0.0         0.0        0.0   0.0          0.0   
#glazunov                       0.0         0.0        0.0   0.0          0.0   
#goncharova                     0.0         0.0        0.0   0.0          0.0   
#gor'kie                        0.0         0.0        0.0   0.0          0.0   
#gor'kij                        0.0         0.0        0.0   0.0          0.0   
#guchkov                        0.0         0.0        

# ДАЛЬШЕ ПОКА НИЧЕГО НЕ НАПИСАНО

In [37]:
mentions_table.sum()

#abramovich                 8.0
#adamovich                 12.0
#afonskij                   4.0
#aga                        5.0
#ajhenval'd                 1.0
#al'tshulera                0.0
#aldanov                    0.0
#aldanovy                   0.0
#aleksinskaja               0.0
#amfiteatrov                3.0
#aminad                     0.0
#bal'mont                  34.0
#baratov                    2.0
#beek                       0.0
#belich                    13.0
#beljaev                    3.0
#berberova                  6.0
#brezhnev                   3.0
#brezhnevy                  0.0
#bunakov-fondaminskij       0.0
#bunin                     81.0
#bunina                     0.0
#buniny                     0.0
#burd                       0.0
#chasing                    1.0
#chirikov                   2.0
#dali                       0.0
#demidov                   15.0
#demidova                   4.0
#denikin                    3.0
#dioneo                     0.0
#don-ami